In [ ]:
!pip install litellm==1.67.2 -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 114.5 MB/s eta 0:00:00


In [ ]:

def enrich_df_with_duration_in_minutes(df, col_name, output_name):
    """Creates a map from duration strings to approximate minutes."""
    duration_map = {}
    minute = 1
    hour = 60 * minute
    day = 8 * hour
    week = 5 * day
    month = 4 * week  # Approximation
    year = 12 * month # Approximation

    duration_map["10 minutes"] = 10 * minute
    duration_map["30 minutes"] = 30 * minute
    duration_map["1 hour"] = 1 * hour
    duration_map["2 hours"] = 2 * hour
    duration_map["4 hours"] = 4 * hour
    duration_map["8 hours"] = 8 * hour
    duration_map["16 hours"] = 16 * hour
    duration_map["3 days"] = 3 * day
    duration_map["1 week"] = 1 * week
    duration_map["3 weeks"] = 3 * week
    duration_map["6 weeks"] = 6 * week
    duration_map["3 months"] = 3 * month
    duration_map["6 months"] = 6 * month
    duration_map["1 year"] = 1 * year
    duration_map["3 years"] = 3 * year
    duration_map["6 years"] = 6 * year
    duration_map["10 years"] = 10 * year

    df[output_name] = df[col_name].map(duration_map)

    assert df[output_name].isna().sum() == 0

    return df

duration_map = {}
minute = 1
hour = 60 * minute
day = 8 * hour
week = 5 * day
month = 4 * week  # Approximation
year = 12 * month # Approximation

duration_map["10 minutes"] = 10 * minute
duration_map["30 minutes"] = 30 * minute
duration_map["1 hour"] = 1 * hour
duration_map["2 hours"] = 2 * hour
duration_map["4 hours"] = 4 * hour
duration_map["8 hours"] = 8 * hour
duration_map["16 hours"] = 16 * hour
duration_map["3 days"] = 3 * day
duration_map["1 week"] = 1 * week
duration_map["3 weeks"] = 3 * week
duration_map["6 weeks"] = 6 * week
duration_map["3 months"] = 3 * month
duration_map["6 months"] = 6 * month
duration_map["1 year"] = 1 * year
duration_map["3 years"] = 3 * year
duration_map["6 years"] = 6 * year
duration_map["10 years"] = 10 * year

duration_map


In [ ]:

import pandas as pd
import math
import litellm
import json
import os
import wandb
from google.colab import userdata

os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')
os.environ['GEMINI_API_KEY'] = userdata.get('GEMINI_API_KEY')

# Download here: https://docs.google.com/spreadsheets/d/1IUgj9GKNpiRheiaoK1nu6nuXbQJfEfwLOmrl-mRD400/edit?gid=1131861571#gid=1131861571
# Then run in Untilted0.ipynb to add the DWAs
# OR fix the problem forever by adding DWAs in the ground truth
dataset = pd.read_csv("groundtruth_with_dwas.csv")

train_dataset = dataset.iloc[:30].copy()
#test_dataset = dataset.iloc[30:]

train_dataset = enrich_df_with_duration_in_minutes(train_dataset, 'Lower bound', 'golden_lower')
train_dataset = enrich_df_with_duration_in_minutes(train_dataset, 'Upper bound', 'golden_upper')

def calc_loss(df):
  df['loss_lower'] = (df['pred_lower'] / df['golden_lower']).map(lambda x: math.log(x)).abs()
  df['loss_upper'] = (df['pred_lower'] / df['golden_upper']).map(lambda x: math.log(x)).abs()

  loss = df['loss_lower'].mean() + df['loss_upper'].mean()
  loss = loss / 2
  loss = math.exp(loss)

  return loss

dataset

Task  \
0   Research equipment or component needs, sources...   
1   Prepare documentation or presentations, includ...   
2   Review material and labor requirements to deci...   
3   Perform administrative duties, such as authori...   
4   Write grant proposals to procure external rese...   
5   Maintain regularly scheduled office hours to a...   
6   Compile, administer, and grade examinations, o...   
7   Maintain regularly scheduled office hours to a...   
8   Compile, administer, and grade examinations, o...   
9   Maintain regularly scheduled office hours to a...   
10  Meet with parents and guardians to discuss the...   
11  Maintain regularly scheduled office hours to a...   
12  Maintain regularly scheduled office hours to a...   
13  Maintain regularly scheduled office hours to a...   
14  Write grant proposals to procure external rese...   
15  Prepare technical and research reports, such a...   
16  Collaborate with colleagues to address teachin...   
17  Compile, administer, and grade examinations, o...   
18  Maintain student attendance records, grades, a...   
19  Maintain regularly scheduled office hours to a...   
20  Initiate, facilitate, and moderate classroom d...   
21  Evaluate data processing proposals to assess p...   
22  Maintain regularly scheduled office hours to a...   
23  Manage subcontractor activities, reviewing pro...   
24  Participate in student recruitment, registrati...   
25  Conduct research in a particular field of know...   
26  Serve on academic or administrative committees...   
27  Locate suppliers, using sources such as catalo...   
28  Consult with institutions or associations rega...   
29  Compile bibliographies of specialized material...   
30  Maintain student attendance records, grades, a...   
31  Prepare course materials, such as syllabi, hom...   
32                          Supervise loan personnel.   
33  Prepare nanotechnology-related invention discl...   
34  Provide professional consulting services to go...   
35  Prepare course materials, such as syllabi, hom...   
36  Assess or propose sustainability initiatives, ...   
37  Create debt management plans, spending plans, ...   
38  Maintain student attendance records, grades, a...   
39  Compile bibliographies of specialized material...   
40  Recommend or execute personnel actions, such a...   
41  Compile and prepare documentation related to p...   
42  Maintain student attendance records, grades, a...   
43  Attend meetings or seminars or read current li...   
44          Research the target audience of projects.   

                                           Occupation  \
0   Electrical and Electronic Engineering Technolo...   
1                          Remote Sensing Technicians   
2                                     Cost Estimators   
3   First-Line Supervisors of Landscaping, Lawn Se...   
4          Biological Science Teachers, Postsecondary   
5   Area, Ethnic, and Cultural Studies Teachers, P...   
6   Family and Consumer Sciences Teachers, Postsec...   
7                 Engineering Teachers, Postsecondary   
8                 Social Work Teachers, Postsecondary   
9   Family and Consumer Sciences Teachers, Postsec...   
10       Special Education Teachers, Secondary School   
11  Anthropology and Archeology Teachers, Postseco...   
12               Architecture Teachers, Postsecondary   
13  Family and Consumer Sciences Teachers, Postsec...   
14    Philosophy and Religion Teachers, Postsecondary   
15                              Industrial Ecologists   
16             Communications Teachers, Postsecondary   
17  Anthropology and Archeology Teachers, Postseco...   
18                   Business Teachers, Postsecondary   
19  Anthropology and Archeology Teachers, Postseco...   
20                  Sociology Teachers, Postsecondary   
21          Computer and Information Systems Managers   
22  Anthropology and Archeology Teachers, Postseco...   
23                                       Logisticians   
2

In [ ]:
wandb.login()

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: felixdorn (felixdorn-forevue) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [ ]:
ALLOWED_DURATIONS = [
    "10 minutes",
    "30 minutes",
    "1 hour",
    "4 hours",
    "8 hours",
    "16 hours",
    "3 days",
    "1 week",
    "3 weeks",
    "6 weeks",
    "3 months",
    "6 months",
    "1 year",
    "3 years",
    "6 years",
    "10 years",
]

SCHEMA = {
    "name": "get_time_estimate",
    "strict": True,
    "schema": {
        "type": "object",
        "properties": {
            "thinking": {"type": "string"},
            "lower_bound_estimate": {"type": "string", "enum": ALLOWED_DURATIONS},
            "upper_bound_estimate": {"type": "string", "enum": ALLOWED_DURATIONS},
        },
        "additionalProperties": False,
        "required": ["thinking", "lower_bound_estimate", "upper_bound_estimate"],
    },
}

def run_llm(df, model, system_prompt, user_message_template):
   messages = [[
        {"role": "system", "content": system_prompt},
        {"role": "user", "content": user_message_template.format(row=row[1])},
    ] for row in df.iterrows()]
   responses = litellm.batch_completion(
            model=model,
            messages=[messages[0]],
            response_format={"type": "json_schema", "json_schema": SCHEMA},
   )

   lb_estimates = []
   ub_estimates = []
   for response in responses:
      lb_estimate = None
      ub_estimate = None

      if (
        hasattr(response, "choices")
        and response.choices
        and hasattr(response.choices[0], "message")
        and response.choices[0].message
        and hasattr(response.choices[0].message, "content")
        and response.choices[0].message.content
      ):
        raw_estimate = response.choices[0].message.content
        estimate = json.loads(raw_estimate)
        print(estimate)
        lb_estimate = estimate.get("lower_bound_estimate")
        ub_estimate = estimate.get("upper_bound_estimate")
      else:
        print(f"Warning: Received non-standard or error response. Response: {response}")


   df["pred_lower_text"] = lb_estimate
   df["pred_upper_text"] = ub_estimate

   df = enrich_df_with_duration_in_minutes(df, "pred_lower_text", "pred_lower")
   df = enrich_df_with_duration_in_minutes(df, "pred_upper_text", "pred_upper")

   return df

In [ ]:
datasets = {}

def run(fn, **kwargs):
  run_data = wandb.init(
      project="sprint-econtain",
      config=kwargs,
  )

  try:
    dataset = train_dataset.copy()

    print(f"Running {run_data.name}")
    fn(df=dataset, **kwargs)
    print(f"Finished {run_data.name}")
    loss = calc_loss(dataset)

    print(f"Loss {run_data.name}:", loss)
    wandb.summary["loss"] = loss

    datasets[run_data.name] = dataset
    return dataset
  except Exception as e:
    wandb.log({"error": str(e)})
    raise e
  finally:
    wandb.finish()

In [ ]:
SYSTEM_PROMPT = """
You are an expert assistant evaluating the time required for job tasks. Your goal is to estimate the 'effective time' range needed for a skilled human to complete the following job task **remotely**, without supervision[cite: 2, 8, 44].

'Effective time' is the active, focused work duration required to complete the task[cite: 2]. Crucially, **exclude all waiting periods, delays, or time spent on other unrelated activities**[cite: 2, 3]. Think of it as the continuous, productive time investment needed if the worker could pause and resume instantly without cost[cite: 3]. This duration serves as a proxy for the level of 'agency' or sustained, coherent effort the task demands[cite: 11, 44].

Provide a lower and upper bound estimate for the 'effective time'. These bounds should capture the time within which approximately 80% of instances of performing this specific task are typically completed by a qualified individual[cite: 2].

- A **job task** is an occupation-specific unit of work.
- **Detailed work activities (DWAs)** are the specific actions comprising the task.

You MUST select your lower and upper bound estimates **only** from the following discrete durations:
['10 minutes', '30 minutes', '1 hour', '2 hours', '4 hours', '8 hours', '16 hours', '3 days', '1 week', '3 weeks', '6 weeks', '3 months', '6 months', '1 year', '3 years', '10 years']

Base your estimate on the provided task description, its associated activities, and the occupational context.
"""

USER_MESSAGE_TEMPLATE = """
Please estimate the effective time range for the following remote task:

**Occupation Category:** {row[Occupation]}
**Occupation Description:** {row[Occupation Description]}

**Task Description:** {row[Task]}
**Detailed Work Activities (DWAs):**
{row[dwas]}

Consider the complexity, required focus, and the typical steps involved as described in the DWAs when determining the active work duration.
"""

run(run_llm, model="openai/gpt-4.1-mini", system_prompt=SYSTEM_PROMPT, user_message_template=USER_MESSAGE_TEMPLATE)

Running clean-waterfall-29
{'thinking': 'The task involves researching equipment or component needs, including sourcing information such as competitive prices, delivery times, and operational costs, as well as estimating technical or resource requirements. This requires focused research, data gathering from multiple sources (like suppliers and technical databases), comparative analysis, and calculation of requirements likely documented for engineering review. For an experienced engineering technologist doing this remotely, the task can vary in complexity depending on how many components or pieces of equipment need evaluation. Typically, this kind of detailed research and estimation could be accomplished in a concentrated span ranging from a half hour (for simpler or single-item research) to up to 4 hours (for more involved multiple component analysis and detailed resource estimation). Thus, an effective time range of 30 minutes to 4 hours best captures typical variation in effort and c

Task  \
0   Research equipment or component needs, sources...   
1   Prepare documentation or presentations, includ...   
2   Review material and labor requirements to deci...   
3   Perform administrative duties, such as authori...   
4   Write grant proposals to procure external rese...   
5   Maintain regularly scheduled office hours to a...   
6   Compile, administer, and grade examinations, o...   
7   Maintain regularly scheduled office hours to a...   
8   Compile, administer, and grade examinations, o...   
9   Maintain regularly scheduled office hours to a...   
10  Meet with parents and guardians to discuss the...   
11  Maintain regularly scheduled office hours to a...   
12  Maintain regularly scheduled office hours to a...   
13  Maintain regularly scheduled office hours to a...   
14  Write grant proposals to procure external rese...   
15  Prepare technical and research reports, such a...   
16  Collaborate with colleagues to address teachin...   
17  Compile, administer, and grade examinations, o...   
18  Maintain student attendance records, grades, a...   
19  Maintain regularly scheduled office hours to a...   
20  Initiate, facilitate, and moderate classroom d...   
21  Evaluate data processing proposals to assess p...   
22  Maintain regularly scheduled office hours to a...   
23  Manage subcontractor activities, reviewing pro...   
24  Participate in student recruitment, registrati...   
25  Conduct research in a particular field of know...   
26  Serve on academic or administrative committees...   
27  Locate suppliers, using sources such as catalo...   
28  Consult with institutions or associations rega...   
29  Compile bibliographies of specialized material...   

                                           Occupation  \
0   Electrical and Electronic Engineering Technolo...   
1                          Remote Sensing Technicians   
2                                     Cost Estimators   
3   First-Line Supervisors of Landscaping, Lawn Se...   
4          Biological Science Teachers, Postsecondary   
5   Area, Ethnic, and Cultural Studies Teachers, P...   
6   Family and Consumer Sciences Teachers, Postsec...   
7                 Engineering Teachers, Postsecondary   
8                 Social Work Teachers, Postsecondary   
9   Family and Consumer Sciences Teachers, Postsec...   
10       Special Education Teachers, Secondary School   
11  Anthropology and Archeology Teachers, Postseco...   
12               Architecture Teachers, Postsecondary   
13  Family and Consumer Sciences Teachers, Postsec...   
14    Philosophy and Religion Teachers, Postsecondary   
15                              Industrial Ecologists   
16             Communications Teachers, Postsecondary   
17  Anthropology and Archeology Teachers, Postseco...   
18                   Business Teachers, Postsecondary   
19  Anthropology and Archeology Teachers, Postseco...   
20                  Sociology Teachers, Postsecondary   
21          Computer and Information Systems Managers   
22  Anthropology and Archeology Teachers, Postseco...   
23                                       Logisticians   
24      Agricultural Sciences Teachers, Postsecondary   
25                Engineering Teachers, Postsecondary   
26                Engineering Teachers, Postsecondary   
27                                 Procurement Clerks   
28                                  Registered Nurses   
29  Criminal Justice and Law Enforcement Teachers,...   

                               Occupation Description Lower bound Upper bound  \
0   Apply electrical and electronic theory and rel...  30 minutes      3 days   
1   Apply remote sensing technologies to assist sc...     2 hours      1 week   
2   Prepare cost estimates for product manufacturi...     4 hours      1 week   
3   Directly supervise and coordinate activities o...     2 hours     8 hours   
4   Teach courses in biological sciences. Includes...      1 week    6 months   
5   Teach courses pertainin

In [ ]:
datasets = {}